# MA8404 Exercise set 4

## Problem 1

Given the Hamiltonian $H(p,q)=\frac{1}{2}p^2+V(q)$ with $V(q)=(1-e^{-q})^2$, the corresponding canonical equations becomes
$$
 q' = p, \qquad p' = -2e^{-q}(1-e^{-q}).
$$
This to be solved by Eulers, Runge-Kutta 4 and Störmer-Verlet's methods. 

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
newparams = {'figure.figsize': (12.0, 6.0), 'axes.grid': True,
             'lines.markersize': 8, 'lines.linewidth': 2,
             'font.size': 14}
plt.rcParams.update(newparams)

In [ ]:
# Implement the methods.

# Forward Euler
def euler(f, t0, tend, y0, Nsteps=100):
    m = len(y0)
    yn = np.zeros((Nsteps+1,m))
    yn[0,:]=y0
    t = np.linspace(t0,tend,Nsteps+1)
    h = t[1]-t[0]
    for n in range(Nsteps):
        yn[n+1,:] = yn[n,:] + h*f(yn[n,:])
    return t, yn

# RK4
def rk4(f, t0, tend, y0, Nsteps=100):
    m = len(y0)
    yn = np.zeros((Nsteps+1,m))
    yn[0,:]=y0
    t = np.linspace(t0,tend,Nsteps+1)
    h = t[1]-t[0]
    for n in range(Nsteps):
        yt = yn[n,:]
        k1 = f(yt)
        k2 = f(yt+0.5*h*k1)
        k3 = f(yt+0.5*h*k2)
        k4 = f(yt+h*k3)
        yn[n+1,:] = yt + h*(k1+2*k2+2*k3+k4)/6
    return t, yn

# Stormer-Verlet
def stormer_verlet(f1, f2, t0, tend, y0, Nsteps=100):
    m = len(y0)
    yn = np.zeros((Nsteps+1,m))
    yn[0,:] = y0
    t = np.linspace(t0,tend,Nsteps+1)
    h = t[1]-t[0]
    for n in range(Nsteps):
        # NB: This implementation only works for separable systems. 
        ytmp = yn[n,:] + 0.5*h*f1(yn[n,:])
        ytmp = ytmp + h*f2(ytmp)
        yn[n+1,:]= ytmp + 0.5*h*f1(ytmp)
    return t, yn

Define the problem. There are two implementions here, one for the standard methods, and a split one for the Störmer-Verlet methods. 

In [ ]:
# Right hand side, with y=[q,p]
def f(y):
    return np.array([y[1],-2*np.exp(-y[0])*(1-np.exp(-y[0]))])

# The Hamiltonian
def H(y):
    return 0.5*y[:,1]**2+(1-np.exp(-y[:,0]))**2

# And similar for the split system: 
def f1(y):
    return np.array([y[1],0])
def f2(y):
    return np.array([0, -2*np.exp(-y[0])*(1-np.exp(-y[0]))])

To really see the difference in the quality in the solution, we solve the problem up to $t=200$, using 1000 steps. You can experiment with this, of course. Euler's method is allowed 4 times as many steps as the others, but is still completely unstable. How many steps do you need with Euler's method to get something sensible? 

In [ ]:
plt.subplot(3,1,1)
Nsteps = 1000
te, ye = euler(f, 0, 200, [1,1], Nsteps=4*Nsteps)
plt.plot(te, ye);

plt.subplot(3,1,2)
trk4, yrk4 = rk4(f, 0, 200, [1,1], Nsteps=Nsteps)
plt.plot(trk4, yrk4);

plt.subplot(3,1,3)
tsv, ysv = stormer_verlet(f1, f2, 0, 200, [1,1], Nsteps=Nsteps)
plt.plot(tsv,ysv);

Notice that for the oscillations, the amplitude is slowly decreasing in the case of the RK4 method, while this do not seem to be the case for the Störmer-Verlet method. You may increase the integration interval to confirm this behavious (increase the number of steps accordingly). 

Let us next plot the Hamiltonian.

In [ ]:
# and plot the Hamiltonian
# plt.plot(te, H(ye), label='Euler')
plt.plot(trk4, H(yrk4), label='RK4')
plt.plot(tsv, H(ysv), label='Störmer-Verlet')
plt.legend()
plt.xlabel('t')
plt.title('Hamiltonian');

Even if the actual error in the Hamiltonian in the Störmer-Verlet case is larger, there is no drift, in contrary to what we observe in the RK4 case. 

And please go ahead and make your own experiments. 

## Problem 5d)

Only the Störmer-Verlet method is implemented here. It should be straightforward to modify the code for the symplectic Euler method, so this is left for you. 


In [ ]:
# Time dependent Störmer-Verlet
def svt(Vq, t0, tend, p0, q0, Nsteps=100):
    m = len(p0)
    qn = np.zeros((Nsteps+1,m))
    pn = np.zeros((Nsteps+1,m))
    qn[0,:]=q0
    pn[0,:]=p0
    t = np.linspace(t0,tend,Nsteps+1)
    h = t[1]-t[0]
    kq = Vq(qn[0,:],t0)
    for n in range(Nsteps):
        ptmp = pn[n,:] - 0.5*h*kq
        qn[n+1,:] = qn[n,:] + h*ptmp
        kq = Vq(qn[n+1,:],t[n+1])
        pn[n+1] = ptmp - 0.5*h*kq
    return t, qn, pn

In [ ]:
# Define Vq
def Vq(q,t):
    epsilon = 0.25
    alpha = 0.1
    return (1+epsilon*np.sin(alpha*t))*q  

# The Hamiltonian:
def H1(p,q,t):
    epsilon = 0.25
    alpha = 0.1
    Nsteps = len(t)-1
    hamilton = np.zeros(Nsteps+1)
    for n in range(Nsteps+1):
        hamilton[n] = 0.5*np.dot(p[n,:],p[n,:])+0.5*(1+epsilon*np.sin(alpha*t[n]))*np.dot(q[n,:],q[n,:])
    return hamilton

Here, the integration interval is chosen to two periods of $\sin (\alpha t)$ to get a better see what is going on. Du to the time variable parameter, both the amplitude and the frequency of the oscillations will change over time. Change the integration interval to see the long term behaviour yourself. 


In [ ]:
# Solve the problem, and plot the result
t0, tend = 0, 40*np.pi
q0, p0 = [1,2,3,4],[4,1,2,3]
t, q, p = svt(Vq,  t0, tend, q0, p0, Nsteps=1000)
plt.plot(t,q[:,0]);

We notice that also the Hamiltonian varies with time, which is expected. 

In [ ]:
plt.plot(t,H1(p,q,t))
plt.title('The Hamiltonian')
plt.xlabel('t')